In [6]:
import os
import sys
from tqdm import tqdm
import pprint
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import umap

from sklearn.metrics import accuracy_score, balanced_accuracy_score, precision_score, recall_score, f1_score, confusion_matrix, roc_auc_score

import torch
from torch.utils.data import DataLoader
import torch.nn.functional as F

sys.path.append('..')
from semilearn.core.utils import get_net_builder, get_dataset, over_write_args_from_file
from semilearn.algorithms.openmatch.openmatch import OpenMatchNet
from semilearn.algorithms.iomatch.iomatch import IOMatchNet

In [7]:
import argparse

parser = argparse.ArgumentParser()
parser.add_argument('--c', type=str, default='')

def load_model_at(step='best'):
    args.step = step
    if step == 'best':
        args.load_path = '/'.join(args.load_path.split('/')[1:-1]) + "/model_best.pth"
    if step == 'latest':
        #args.load_path = '/'.join(args.load_path.split('/')[:-1]) + "/model_at_{args.step}_step.pth"
        args.load_path = '/'.join(args.load_path.split('/')[:-1]) + "/latest_model.pth"
    else:
        args.load_path = '/'.join(args.load_path.split('/')[:-1]) + "/"+str(step)+"_model.pth"
        
    print(args.load_path)
    checkpoint_path = os.path.join(args.load_path)
    checkpoint = torch.load(checkpoint_path)
    load_model = checkpoint['ema_model']
    load_state_dict = {}
    for key, item in load_model.items():
        if key.startswith('module'):
            new_key = '.'.join(key.split('.')[1:])
            load_state_dict[new_key] = item
        else:
            load_state_dict[key] = item
    save_dir = '/'.join(checkpoint_path.split('/')[:-1])
    if step == 'best':
        args.save_dir = os.path.join(save_dir, f"model_best")
    else:
        args.save_dir = os.path.join(save_dir, f"step_{args.step}")
    os.makedirs(args.save_dir, exist_ok=True)
    _net_builder = get_net_builder(args.net, args.net_from_name)
    net = _net_builder(num_classes=args.num_classes)
    if args.algorithm == 'openmatch':
        net = OpenMatchNet(net, args.num_classes)
    elif args.algorithm == 'iomatch':
        net = IOMatchNet(net, args.num_classes)
    else:
        raise NotImplementedError
    keys = net.load_state_dict(load_state_dict)
    print(f'Model at step {args.step} loaded!')
    if torch.cuda.is_available():
        net.cuda()
    net.eval()
    
    return net

In [8]:
def evaluate_open(net, dataset_dict, num_classes, extended_test=False):
    full_loader = DataLoader(dataset_dict['test']['full'], batch_size=256, drop_last=False, shuffle=False, num_workers=1)
    if extended_test:
        extended_loader = DataLoader(dataset_dict['test']['extended'], batch_size=1024, drop_last=False, shuffle=False, num_workers=4)

    total_num = 0.0
    y_true_list = []
    y_pred_closed_list = []
    y_pred_ova_list = []
    
    results = {}
    
    with torch.no_grad():
        for data in tqdm(full_loader):
            x = data['x_lb']
            y = data['y_lb']

            if isinstance(x, dict):
                x = {k: v.cuda() for k, v in x.items()}
            else:
                x = x.cuda()
            y = y.cuda()

            num_batch = y.shape[0]
            total_num += num_batch
            
            out = net(x)
            logits, logits_open = out['logits'], out['logits_open']    
            pred_closed = logits.data.max(1)[1]
            
            probs = F.softmax(logits, 1)
            probs_open = F.softmax(logits_open.view(logits_open.size(0), 2, -1), 1)
            tmp_range = torch.arange(0, logits_open.size(0)).long().cuda()
            unk_score = probs_open[tmp_range, 0, pred_closed]
            pred_open = pred_closed.clone()
            pred_open[unk_score > 0.5] = num_classes

            y_true_list.extend(y.cpu().tolist())
            y_pred_closed_list.extend(pred_closed.cpu().tolist())
            y_pred_ova_list.extend(pred_open.cpu().tolist())

    y_true = np.array(y_true_list)

    closed_mask = y_true < num_classes
    open_mask = y_true >= num_classes
    y_true[open_mask] = num_classes

    y_pred_closed = np.array(y_pred_closed_list)
    y_pred_ova = np.array(y_pred_ova_list)

    # Closed Accuracy on Closed Test Data
    y_true_closed = y_true[closed_mask]
    y_pred_closed = y_pred_closed[closed_mask]
    closed_acc = accuracy_score(y_true_closed, y_pred_closed)
    closed_cfmat = confusion_matrix(y_true_closed, y_pred_closed, normalize='true')
    results['c_acc_c_p'] = closed_acc
    results['c_cfmat_c_p'] = closed_cfmat  

    # Open Accuracy on Full Test Data
    open_acc = balanced_accuracy_score(y_true, y_pred_ova)
    open_cfmat = confusion_matrix(y_true, y_pred_ova)
    results['o_acc_f_hq'] = open_acc  
    results['o_cfmat_f_hq'] = open_cfmat
        
    if extended_test:
        with torch.no_grad():
            for data in tqdm(extended_loader):
                x = data['x_lb']
                y = data['y_lb']

                if isinstance(x, dict):
                    x = {k: v.cuda() for k, v in x.items()}
                else:
                    x = x.cuda()
                y = y.cuda()

                num_batch = y.shape[0]
                total_num += num_batch

                out = net(x)
                logits, logits_open = out['logits'], out['logits_open']    
                pred_closed = logits.data.max(1)[1]

                probs = F.softmax(logits, 1)
                probs_open = F.softmax(logits_open.view(logits_open.size(0), 2, -1), 1)
                tmp_range = torch.arange(0, logits_open.size(0)).long().cuda()
                unk_score = probs_open[tmp_range, 0, pred_closed]
                pred_open = pred_closed.clone()
                pred_open[unk_score > 0.5] = num_classes

                y_true_list.extend(y.cpu().tolist())
                y_pred_closed_list.extend(pred_closed.cpu().tolist())
                y_pred_ova_list.extend(pred_open.cpu().tolist())
            
        y_true = np.array(y_true_list)

        open_mask = y_true >= num_classes
        y_true[open_mask] = num_classes
        y_pred_ova = np.array(y_pred_ova_list)
        
        # Open Accuracy on Extended Test Data
        open_acc = balanced_accuracy_score(y_true, y_pred_ova)
        open_cfmat = confusion_matrix(y_true, y_pred_ova, normalize='true')
        results['o_acc_e_hq'] = open_acc  
        results['o_cfmat_e_hq'] = open_cfmat
    
    print(f"#############################################################\n"
              f" Closed Accuracy on Closed Test Data: {results['c_acc_c_p'] * 100:.2f}\n"
              f" Open Accuracy on Full Test Data:     {results['o_acc_f_hq'] * 100:.2f}\n"
              #f" Open Accuracy on Extended Test Data: {results['o_acc_e_hq'] * 100:.2f}\n"
              f"#############################################################\n"
        )
    
    return results

In [9]:
def evaluate_io(args, net, dataset_dict, extended_test=False):
    """
    evaluation function for open-set SSL setting
    """

    full_loader = DataLoader(dataset_dict['train_ulb'], batch_size=256, drop_last=False, shuffle=False, num_workers=1)
    if extended_test:
        extended_loader = DataLoader(dataset_dict['test']['extended'], batch_size=1024, drop_last=False, shuffle=False, num_workers=4)

    total_num = 0.0
    y_true_list = []
    p_list = []
    pred_p_list = []
    pred_hat_q_list = []
    pred_q_list = []
    pred_q_prob_list=[]
    pred_hat_p_list = []

    with torch.no_grad():
        for data in tqdm(full_loader):
            x = data['x_ulb_w']
            y = data['y_ulb']
            print('y',len(y),y)
            
            if isinstance(x, dict):
                x = {k: v.cuda() for k, v in x.items()}
            else:
                x = x.cuda()
            y = y.cuda()
            y_true_list.extend(y.cpu().tolist())

            num_batch = y.shape[0]
            total_num += num_batch

            outputs = net(x)
            logits = outputs['logits']
            logits_mb = outputs['logits_mb']
            logits_open = outputs['logits_open']

            # predictions p of closed-set classifier
            p = F.softmax(logits, 1)
            pred_p = p.data.max(1)[1]
            pred_p_list.extend(pred_p.cpu().tolist())

            # predictions hat_q from (closed-set + multi-binary) classifiers
            r = F.softmax(logits_mb.view(logits_mb.size(0), 2, -1), 1)
            tmp_range = torch.arange(0, logits_mb.size(0)).long().cuda()
            hat_q = torch.zeros((num_batch, args.num_classes + 1)).cuda()
            o_neg = r[tmp_range, 0, :]
            o_pos = r[tmp_range, 1, :]
            hat_q[:, :args.num_classes] = p * o_pos
            hat_q[:, args.num_classes] = torch.sum(p * o_neg, 1)
            pred_hat_q = hat_q.data.max(1)[1]
            pred_hat_q_list.extend(pred_hat_q.cpu().tolist())

            # predictions q of open-set classifier
            q = F.softmax(logits_open, 1)
            pred_q = q.data.max(1)[1]
            print('p',p[0],'o_pos',o_pos[0])
            print('q.data',q.data[0:10])
            print('hatq.data',hat_q.data[0:10])
            print('pred_q',pred_q)
            pred_q_prob = q.data
            pred_q_list.extend(pred_q.cpu().tolist())
            pred_q_prob_list.extend(pred_q_prob)

            # prediction hat_p of open-set classifier
            hat_p = q[:, :args.num_classes] / q[:, :args.num_classes].sum(1).unsqueeze(1)
            pred_hat_p = hat_p.data.max(1)[1]
            pred_hat_p_list.extend(pred_hat_p.cpu().tolist())

        y_true = np.array(y_true_list)
        #print('y_true',len(y_true),y_true)
        closed_mask = y_true < args.num_classes
        open_mask = y_true >= args.num_classes
        #y_true[open_mask] = args.num_classes
        #print('pred_q[censys_index]',pred_q[censys_index])

        pred_p = np.array(pred_p_list)
        pred_hat_p = np.array(pred_hat_p_list)
        pred_q = np.array(pred_q_list)
        pred_hat_q = np.array(pred_hat_q_list)
        
        # closed accuracy of p / hat_p on closed test data
        c_acc_c_p = accuracy_score(y_true[closed_mask], pred_p[closed_mask])
        c_acc_c_hp = accuracy_score(y_true[closed_mask], pred_hat_p[closed_mask])
        set_label =  ['adscore',
 'ahrefs',
 'arbor',
 'archive',
 'binaryedge',

 'criminalip',
 'cybergreen',

 'fofa',
 'internet_census',
 'internettl',
 'intrinsec',
 'ipip',
 'leakix',
 'onyphe',
 'quadmetrics',
 'quake',
 'rapid7',
 'rau',
 'shadowserver',
 'shodan',
 'stretchoid',
 'tum',
 'webRay',
 'x_threatbook',
 'zoomeye',
'driftnet(added in unknown)',
 'unknown',
 'censys(added in unknown)'                     ]
 
        c_cfmat_c_p = confusion_matrix(y_true[closed_mask], pred_p[closed_mask])
        
        
        
        print('y_true[closed_mask]',y_true[closed_mask])
        print('pred_hat_p[closed_mask]',pred_hat_p[closed_mask])
        c_cfmat_c_hp = confusion_matrix(y_true[closed_mask], pred_hat_p[closed_mask], normalize='true')
        np.set_printoptions(precision=3, suppress=True)

        # open accuracy of q / hat_q on full test data
        o_acc_f_q = balanced_accuracy_score(y_true, pred_q)
        o_acc_f_q_f = f1_score(y_true, pred_q,average='weighted')
        o_acc_f_hq = balanced_accuracy_score(y_true, pred_hat_q)
        o_acc_f_hq_f = f1_score(y_true, pred_hat_q,average='weighted')
        o_cfmat_f_q = confusion_matrix(y_true, pred_q)
        o_cfmat_f_hq = confusion_matrix(y_true, pred_hat_q)
        
   
        index_list=list(set(y_true)|set(pred_q))
        label_list=[]
        for item in index_list:
            label_list.append(set_label[item])

    
        y_true_arr = y_true.copy()
        
        
        value_to_delete = 26
        
        mask = y_true != value_to_delete
        filtered_y_true = y_true_arr[mask]
        filtered_pred_q = pred_q[mask]
        o_acc_f_q_filtered = balanced_accuracy_score(filtered_y_true, filtered_pred_q)
        y_true_arr[open_mask] = args.num_classes
        filtered_y_true_open_masked = y_true_arr[mask]
        o_acc_f_q_filtered_masked = balanced_accuracy_score(filtered_y_true_open_masked, filtered_pred_q)
        
        print('o_acc_f_q_filtered',o_acc_f_q_filtered) 
        print('o_acc_f_q_filtered_masked',o_acc_f_q_filtered_masked)

        o_acc_e_q = o_acc_e_hq = 0
        o_cfmat_e_q = None
        o_cfmat_e_hq = None

        if extended_test:
            unk_scores = []
            unk_scores_q = []
            for data in tqdm(extended_loader):
                x = data['x_lb']
                y = data['y_lb']

                if isinstance(x, dict):
                    x = {k: v.cuda() for k, v in x.items()}
                else:
                    x = x.cuda()
                y = y.cuda()
                y_true_list.extend(y.cpu().tolist())

                num_batch = y.shape[0]
                total_num += num_batch

                outputs = net(x)
                logits = outputs['logits']
                logits_mb = outputs['logits_mb']
                logits_open = outputs['logits_open']

                # predictions p of closed-set classifier
                p = F.softmax(logits, 1)
                pred_p = p.data.max(1)[1]
                pred_p_list.extend(pred_p.cpu().tolist())

                # predictions hat_q of (closed-set + multi-binary) classifiers
                r = F.softmax(logits_mb.view(logits_mb.size(0), 2, -1), 1)
                tmp_range = torch.arange(0, logits_mb.size(0)).long().cuda()
                hat_q = torch.zeros((num_batch, args.num_classes + 1)).cuda()
                o_neg = r[tmp_range, 0, :]
                o_pos = r[tmp_range, 1, :]
                unk_score = torch.sum(p * o_neg, 1)
                hat_q[:, :args.num_classes] = p * o_pos
                hat_q[:, args.num_classes] = torch.sum(p * o_neg, 1)
                pred_hat_q = hat_q.data.max(1)[1]
                pred_hat_q_list.extend(pred_hat_q.cpu().tolist())

                # predictions q of open-set classifier
                q = F.softmax(logits_open, 1)
                pred_q = q.data.max(1)[1]
                pred_q_list.extend(pred_q.cpu().tolist())

                # prediction hat_p of open-set classifier
                hat_p = q[:, :args.num_classes] / q[:, :args.num_classes].sum(1).unsqueeze(1)
                pred_hat_p = hat_p.data.max(1)[1]
                pred_hat_p_list.extend(pred_hat_p.cpu().tolist())

            y_true = np.array(y_true_list)
            open_mask = y_true >= args.num_classes
            y_true[open_mask] = args.num_classes

            pred_q = np.array(pred_q_list)
            pred_hat_q = np.array(pred_hat_q_list)

            # open accuracy of q / hat_q on extended test data
            o_acc_e_q = balanced_accuracy_score(y_true, pred_q)
            o_acc_e_hq = balanced_accuracy_score(y_true, pred_hat_q)
            o_cfmat_e_q = confusion_matrix(y_true, pred_q, normalize='true')
            o_cfmat_e_hq = confusion_matrix(y_true, pred_hat_q, normalize='true')

        eval_dict = {'c_acc_c_p': c_acc_c_p, 'c_acc_c_hp': c_acc_c_hp,
                     'o_acc_f_q': o_acc_f_q, 'o_acc_f_hq': o_acc_f_hq,
                     'o_acc_e_q': o_acc_e_q, 'o_acc_e_hq': o_acc_e_hq,
                     'c_cfmat_c_p': c_cfmat_c_p, 'c_cfmat_c_hp': c_cfmat_c_hp,
                     'o_cfmat_f_q': o_cfmat_f_q, 'o_cfmat_f_hq': o_cfmat_f_hq,
                     'o_cfmat_e_q': o_cfmat_e_q, 'o_cfmat_e_hq': o_cfmat_e_hq,
                     'pred_q_prob_list':pred_q_prob_list,
                     'o_acc_f_q_f':o_acc_f_q_f,
                     'label_list':label_list,
                     'o_acc_f_q_filtered':o_acc_f_q_filtered,
                     'pred_q':pred_q,
                     'pred_p':pred_p,
                     'y_true':y_true
                    }
        print('fscore',o_acc_f_q_f,'f_hq',o_acc_f_hq_f)
        print(f"#############################################################\n"
              f" Closed Accuracy on Closed Test Data (p / hp): {c_acc_c_p * 100:.2f} / {c_acc_c_hp * 100:.2f}\n"
              f" Open Accuracy on Full Test Data (q / hq):     {o_acc_f_q * 100:.2f} / {o_acc_f_hq * 100:.2f}\n"
              f" Open Accuracy on Extended Test Data (q / hq): {o_acc_e_q * 100:.2f} / {o_acc_e_hq * 100:.2f}\n"
              f"#############################################################\n"
            )

        return eval_dict

In [15]:
import numpy as np
import pandas as pd
import pickle

dataset_name='SelfDeploy24'


for protocol in ['http','tls','dns']:
    if(dataset_name=='SelfDeploy24'):
        dataset='selfdeploy_merge_month_2_4_2weektest'
        name='merge_month_2_4_2week'
        train_ensemble_dir='train_ensemble_batch64'
        earliest_time = pd.to_datetime('2024-01-31 16:00:00')
        latest_time = pd.to_datetime('2024-04-12 16:00:00')
    if(dataset_name=='SelfDeploy25'):
        dataset='selfdeploy_24_25_fulldata_2weektest'
        name='selfdeploy_24_25_2week'
        train_ensemble_dir='train_ensemble_selfdeploy25_batch64'
        earliest_time = pd.to_datetime('2024-12-10 16:00:00') 
        latest_time = pd.to_datetime('2025-02-25 16:00:00')

    config_name='iomatch_exp_'+dataset+'_'+protocol+'.yaml'#iomatch_cifar10_14000_28class_exp_month2_4_http_perservice_40dayscompletetrain_second
    args = parser.parse_args(args=['--c', 'config/openset_cv/iomatch/'+config_name])#test5#iomatch_cifar10_150_eval_25_n#iomatch_cifar10_14000_15class_comp_1
    over_write_args_from_file(args, args.c)#iomatch_cifar10_300_13_2class_comp_1#iomatch_cifar10_14000_13_2class_comp_1
    args.data_dir = 'data'
    total_epoch=250
    batch_size=64
    args.bsz = batch_size
    args.load_path = "./saved_models/openset_cv/iomatch_"+dataset+"_"+protocol+"_extra_ep"+str(total_epoch)+"_bs"+str(batch_size)+"/latest_model.pth"
    
    dataset_dict = get_dataset(args, args.algorithm, args.dataset, args.num_labels, args.num_classes, args.data_dir, eval_open=False)
    best_net = load_model_at('1999')#2199
    eval_dict = evaluate_io(args, best_net, dataset_dict)

    
    if('http' in config_name):
        proto='http'
    if('tls' in config_name):
        proto='tls'
    if('dns' in config_name):
        proto='dns'
    if('ssh' in config_name):
        proto='ssh'
    if('rdp' in config_name):
        proto='rdp'
        
    
    mode='train'
    npy_path1 = '../dataset/npy/ip_array_'+proto+'_'+name+'_'+mode+'.npy'
    #npy_path1 = 'ip_array_'+proto+'_'+name+'_'+mode+'.npy'
    npy_path2 = '../dataset/npy/timestamp_'+proto+'_'+name+'_'+mode+'.npy'
    #dataset = NumpyDataset(npy_path1,npy_path2)
    
    loaded_array = np.load(npy_path1,allow_pickle=True)
    loaded_array
    len(loaded_array)
    loaded_timestamp = np.load(npy_path2,allow_pickle=True)
    
    
    pred = eval_dict['pred_q']
    y_true = eval_dict['y_true']
    df = pd.DataFrame({'prediction': pred, 'ip': loaded_array,'groundtruth':y_true,'timestamp':loaded_timestamp})
    
    print(df)
    
    # A list of honeypot addresses to remove
    ips_to_remove = ['192.168.1.0', '192.168.2.0','192.168.3.0','192.168.4.0','192.168.5.0']
    
    # Removes the row with the specified IP address
    df = df[~df['ip'].isin(ips_to_remove)]
            
    
    df.to_csv('result_'+proto+'_'+name+'_'+mode+'.csv', index=False)
    
    
    import pandas as pd
    
    
    for day_interval in [7]:
    
        df = pd.read_csv('result_'+proto+'_'+name+'_'+mode+'.csv')
        
        
        df['timestamp'] = pd.to_datetime(df['timestamp'])
        
        
        print(f"Earliest time: {earliest_time}")
        print(f"Latest time: {latest_time}")
        
        
        time_range = latest_time - earliest_time
        
        
        num_segments = (time_range.days) // day_interval 
        
        
        segment_dfs = []
        
        
        for i in range(num_segments):
            start_time = earliest_time + pd.Timedelta(days=i * day_interval)
            end_time = earliest_time + pd.Timedelta(days=(i + 1) * day_interval)
            print(start_time,end_time)
            
            segment_df = df[(df['timestamp'] >= start_time) & (df['timestamp'] < end_time)]
            
            
            segment_dfs.append(segment_df)
        
        
        for i, segment_df in enumerate(segment_dfs):
            start_time = earliest_time + pd.Timedelta(days=i * day_interval)
            end_time = earliest_time + pd.Timedelta(days=(i + 1) * day_interval)
            print(f"Segment {i+1} ({start_time} to {end_time}):")
            print(segment_df)
            print("\n")
            
        file_dir=train_ensemble_dir+'/result_'+str(day_interval)+'day_segment_'+proto+'/'
        import os
        
        
        directory = file_dir
        
        
        if not os.path.exists(directory):
            os.mkdir(directory)
            print(f"Directory '{directory}' created.")
        else:
            print(f"Directory '{directory}' already exists.")
            
        
        for i, segment_df in enumerate(segment_dfs):
            segment_df.to_csv(train_ensemble_dir+'/result_'+str(day_interval)+'day_segment_'+proto+f'/segment_{i+1}.csv', index=False)
        
        #The most common of the predicted label is calculated for each ip
        def protocol_level_prediciton(ip_train2,y_train2,train2_label_dic_common):
            a=pd.DataFrame()
            a['ip']=ip_train2
            a['label']=y_train2
            a['pred_label']=None
            a=a.drop_duplicates()
            for index, row in a.iterrows():
                a.loc[index,'pred_label']=train2_label_dic_common[row['ip']]
            return a
        
        import os
        import pandas as pd
        
        
        folder_path = train_ensemble_dir+'/result_'+str(day_interval)+'day_segment_'+proto
        
        
        files = [f for f in os.listdir(folder_path) if f.startswith('seg') and f.endswith('.csv')]
        
        
        dfs = []
        
        for file in files:
            file_path = os.path.join(folder_path, file)
            df = pd.read_csv(file_path)
            dfs.append(df)
        
        dfs_merge_protocol_level={}
        
        for i, df in enumerate(dfs):
            print(f"DataFrame from {files[i]}:")

        
            test_http_label_dic = {}
            for value, group_df in df.groupby('ip'):
                test_http_label_dic[value] = group_df
                
            test_http_label_dic_common={}
            for j in test_http_label_dic.keys():
                test_http_label_dic_common[j]=test_http_label_dic[j]['prediction'].mode().values[0]
            
            df_ip_http_test=protocol_level_prediciton(df['ip'],df['groundtruth'],test_http_label_dic_common)
            df_ip_http_test=df_ip_http_test.rename(columns={'pred_label':'pred_label_'+proto})
            dfs_merge_protocol_level[files[i]]=df_ip_http_test

        with open('proto_level_'+str(day_interval)+'daysegment_pred_'+proto+'_'+name+'_'+mode+'.pkl', 'wb') as f:
            pickle.dump(dfs_merge_protocol_level, f)
         
        dfs_merge_protocol_level

dataset_name merge_month_2_4_2week
data_dir data/cifar10
num_labels 2500 num_classes 25 this mode use all samples
dataset_data (4214, 18, 18, 3)
dataset_data (65480, 18, 18, 3)
len_seen_indices 1029
dataset_data (1029, 18, 18, 3)
dataset_data (13779, 18, 18, 3)
lb_dset <semilearn.datasets.cv_datasets.datasetbase.BasicDataset object at 0x7f9e1e0f6220> lb_dset 4214
./saved_models/openset_cv/iomatch_selfdeploy_merge_month_2_4_2weektest_http_extra_ep250_bs64/1999_model.pth


/tmp/ipykernel_1231105/4148006837.py:18: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(checkpoint_path)


Model at step 1999 loaded!


  0%|▏                                          | 1/256 [00:00<00:35,  7.10it/s]

y 256 tensor([4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4])
p tensor([0.0051, 0.0048, 0.0043, 0.0065, 0.2541, 0.0046, 0.0066, 0.0098, 0.0096,
        0.0087, 0.0058, 0.0064, 0.0088, 0.0034, 0.0066,

...

tensor([[0.0029, 0.0021, 0.0026, 0.0022, 0.0053, 0.0098, 0.0104, 0.0022, 0.0226,
         0.0117, 0.0016, 0.0016, 0.0010, 0.0096, 0.0027, 0.0025, 0.0013, 0.0015,
         0.3158, 0.0083, 0.0133, 0.0328, 0.0020, 0.0016, 0.0077, 0.5247],
        [0.0029, 0.0021, 0.0026, 0.0022, 0.0053, 0.0098, 0.0104, 0.0022, 0.0226,
         0.0117, 0.0016, 0.0016, 0.0010, 0.0096, 0.0027, 0.0025, 0.0013, 0.0015,
         0.3158, 0.0083, 0.0133, 0.0328, 0.0020, 0.0016, 0.0077, 0.5247],
        [0.0029, 0.0021, 0.0026, 0.0022, 0.0053, 0.0098, 0.0104, 0.0022, 0.0226,
         0.0117, 0.0016, 0.0016, 0.0010, 0.0096, 0.0027, 0.0025, 0.0013, 0.0015,
         0.3158, 0.0083, 0.0133, 0.0328, 0.0020, 0.0016, 0.0077, 0.5247],
        [0.0029, 0.0021, 0.0026, 0.0022, 0.0053, 0.0098, 0.0104, 0.0022, 0.0226,
         0.0117, 0.0016, 0.0016, 0.0010, 0.0096, 0.0027, 0.0025, 0.0013, 0.0015,
         0.3158, 0.0083, 0.0133, 0.0328, 0.0020, 0.0016, 0.0077, 0.5247],
        [0.0052, 0.0055, 0.0054, 0.0060, 0.0091, 0.0420,

100%|███████████████████████████████████████████| 49/49 [00:01<00:00, 36.66it/s]
/root/anaconda3/envs/py39/lib/python3.9/site-packages/sklearn/metrics/_classification.py:2480: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
/root/anaconda3/envs/py39/lib/python3.9/site-packages/sklearn/metrics/_classification.py:2480: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")


y_true[closed_mask] [ 4  4  4 ... 24 24 24]
pred_hat_p[closed_mask] [24 24 24 ... 24 24 24]
o_acc_f_q_filtered 0.552133768562262
o_acc_f_q_filtered_masked 0.629056845485339
fscore 0.059811647937413004 f_hq 0.05988709053698215
#############################################################
 Closed Accuracy on Closed Test Data (p / hp): 88.18 / 88.18
 Open Accuracy on Full Test Data (q / hq):     51.27 / 51.27
 Open Accuracy on Extended Test Data (q / hq): 0.00 / 0.00
#############################################################



/root/anaconda3/envs/py39/lib/python3.9/site-packages/sklearn/metrics/_classification.py:2480: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")


       prediction              ip  groundtruth            timestamp
0              25    45.33.95.124            4  2024-02-13 20:39:00
1              25   138.68.16.247            4  2024-02-13 21:02:19
2              25    64.227.12.35            4  2024-03-18 13:41:21
3              25     45.33.94.57            4  2024-03-18 14:03:43
4              25  162.142.125.90           27  2024-02-01 07:55:38
...           ...             ...          ...                  ...
12374          25  118.123.105.93           24  2024-02-17 21:05:15
12375          25   103.56.61.144           24  2024-02-29 02:24:27
12376          25   103.56.61.144           24  2024-03-24 20:17:51
12377          25   103.56.61.144           24  2024-03-24 20:18:18
12378          25  118.123.105.85           24  2024-04-06 10:45:59

[12379 rows x 4 columns]
Earliest time: 2024-01-31 16:00:00
Latest time: 2024-04-12 16:00:00
2024-01-31 16:00:00 2024-02-07 16:00:00
2024-02-07 16:00:00 2024-02-14 16:00:00
2024-02-14